In [13]:
# %%writefile box.py
from copy import deepcopy

class Box:
    def __init__(self, x, y):
        self.coordinates = [(x, y), (x + 1, y), (x, y + 1), (x + 1, y + 1)]
        
        self.XY = (x, y)

        # lines
        self.TopLine = (self.coordinates[0], self.coordinates[1])
        self.LeftLine = (self.coordinates[0], self.coordinates[2])
        self.RightLine = (self.coordinates[1], self.coordinates[3])
        self.BottomLine = (self.coordinates[2], self.coordinates[3])
        # lines 
        self.lines = [self.TopLine, self.LeftLine, self.RightLine, self.BottomLine]

        # lines connection indicator 
        self._top = False
        self._left = False
        self._right = False
        self._bottom = False

        self.owner = None
        self.completed = False

        self.value = 1

    def connect(self, coordinates):
        line = coordinates
        success = False

        if line not in self.lines:
            return False
        
        if line == self.TopLine and self._top is False:
            self._top = True
            success = True
        elif line == self.LeftLine and self._left is False:
            self._left = True
            success = True
        elif line == self.RightLine and self._right is False:
            self._right = True
            success = True
        elif line == self.BottomLine and self._bottom is False:
            self._bottom = True
            success = True

        if self._top == True and self._bottom == True and self._left == True and self._right == True:
            self.completed = True
        
        return success

    def un_connect(self, coordinates):
        line = coordinates
        if line in self.lines:
            self.completed = False
            # self.owner = None

        if line == self.TopLine:
            self._top = False
        elif line == self.LeftLine:
            self._left = False
        elif line == self.RightLine:
            self._right = False
        elif line == self.BottomLine:
            self._bottom = False

        
    def copy(self):
        return deepcopy(self)
    
    def _repr_pretty_(self, p, cycle):
        if cycle:
            pass

        if self._top:
            p.text("*---*")
        else:
            p.text("*   *")
        p.break_()
        if self._left:
            p.text("|")
        else:
            p.text(" ")
        
        if self.completed:
            p.text(f" {self.owner} ")
        else:
            p.text("   ") 

        if self._right:
            p.text("|")

        p.break_()

        if self._bottom:
            p.text("*---*")
        else:
            p.text("*   *")



In [14]:
# %%writefile board.py
from collections import deque
from copy import deepcopy

class Board:
    display_single_box = False

    def __init__(self, m, n):
        self.player_score = 0
        self.ai_score = 0
        self.m = m
        self.n = n
        self._boxes = self._generate_boxes(m, n)
        self._open_vectors = self._generate_vectors(m, n)
        self._moves = []
        # Verificar si los vectores se generaron correctamente
        #print(f"Open Vectors Initialized: {self._open_vectors}")

    def _generate_boxes(self, rows, cols):
        """
        This function generates the boxes of the board
        """
        boxes = [[Box(x, y) for x in range(cols)] for y in range(rows)]

        return boxes
    
    def _generate_vectors(self, m, n):
        '''
        The vectors represent the available moves, or lines, which can
        be played on a game board of m rows and n columns. These are stored as tuples
        containing each coordinate and are stored in a queue. The vector queue, along
        with the list of boxes that correspond to the coordinates, are used to represent
        game state.
        Vector format: ((x1, y1), (x2, y2)).

        The vectors always point away from the origin (0, 0), so moving like (1, 0) => (0, 0)
        is not a valid move while (0, 0) => (1, 0) is a valid move
        '''
        vectors = set()
        for i in range(0, m + 1):
            for j in range(0, n):
                # Adding horizontal line vectors
                vectors.add(((j, i), (j + 1, i)))
                # Adding vertical line vectors if not in the last row
                if i < m:
                    vectors.add(((j, i), (j, i + 1)))
            # Adding the vertical line for the last column in the current row
            if i < m:
                vectors.add(((n, i), (n, i + 1)))
        return vectors

    def is_valid_move(self, coordinates):
        return coordinates in self._open_vectors

    
    def move(self, coordinates, player_move: bool = False, is_simulation: bool = False):
        if not self.is_valid_move(coordinates):
            print(f"Invalid move attempted: {coordinates}")
            return False

        if is_simulation:
            print(f"Simulating move: {coordinates} by {'Player' if player_move else 'AI'}")
        else:
            print(f"Attempting move: {coordinates} by {'Player' if player_move else 'AI'}")
        
        print(f"Available moves before: {self._open_vectors}")
        
        player = "P" if player_move else "A"
        
        self._open_vectors.remove(coordinates)
        self._moves.append(coordinates)
        closed = self._checkboxes(coordinates, player)
        
        print(f"Available moves after: {self._open_vectors}")
        print(f"Move resulted in closing box: {closed}")
        
        return closed



    def undo_last_move(self):
        if self._moves:
            move = self._moves.pop()
            self._open_vectors.add(move)
            self._undo_move_on_boxes(move)

    def _undo_move_on_boxes(self, move):
        for i in range(self.m):
            for j in range(self.n):
                box = self._boxes[i][j]
                if move in box.lines:
                    self._undo_box_completion(box, move)

    def _undo_box_completion(self, box, move):
        if box.completed:
            self._adjust_scores(box)
            box.owner = None
        box.un_connect(move)

    def _adjust_scores(self, box):
        if box.owner == "P":
            self.player_score -= 1
        else:
            self.ai_score -= 1               
        
    def has_moves(self):
        return bool(self._open_vectors)

    def get_available_moves(self):
        return self._open_vectors
        
    def _checkboxes(self, coordinates, player: str):
        closed = None
        for i in range(self.m):
            for j in range(self.n):
                box = self._boxes[i][j]
                if coordinates in box.lines:
                    box.connect(coordinates)
                if box.completed == True and box.owner == None:
                    box.owner = player
                    if player == "P":
                        self.player_score += 1
                    else:
                        self.ai_score += 1
                    closed = True
        return closed

    
    def copy(self):
        return deepcopy(self)
    
    def display_board(self):
        # Display player scores
        print(f"Player 1: {self.player_score}")
        print(f"Player AI: {self.ai_score}\n")

        for i in range(self.m):
            top_line, middle_line = self._generate_row_lines(i)
            print(top_line)
            print(middle_line)

        bottom_line = self._generate_bottom_line()
        print(bottom_line)
        print("")  # New line for spacing

    def _generate_row_lines(self, row):
        top_line = "   "  # Start with some spacing for alignment
        middle_line = "   "  # Line below to display vertical lines and boxes

        for j in range(self.n):
            top_line += self._generate_top_line_segment(j, row)
            middle_line += self._generate_middle_line_segment(j, row)

        # Last dot on the right end of the row
        top_line += "*"
        middle_line += "|" if ((self.n, row), (self.n, row + 1)) in self._moves else " "

        return top_line, middle_line

    def _generate_top_line_segment(self, col, row):
        segment = "*"
        if ((col, row), (col + 1, row)) in self._moves:
            segment += "---"
        else:
            segment += "   "
        return segment

    def _generate_middle_line_segment(self, col, row):
        segment = "| " if ((col, row), (col, row + 1)) in self._moves else "  "
        if self._boxes[col][row].completed:
            segment += f"{self._boxes[col][row].owner} "
        else:
            segment += "  "
        return segment

    def _generate_bottom_line(self):
        bottom_line = "   "
        for j in range(self.n):
            bottom_line += "*"
            if ((j, self.m), (j + 1, self.m)) in self._moves:
                bottom_line += "---"
            else:
                bottom_line += "   "
        bottom_line += "*"
        return bottom_line

    def _repr_pretty_(self, p, cycle):
        self.__display_single_box(p)


    def __display_single_box(self, p):
        for i in range(self.m):
            top_line, middle_line = self._generate_row_lines(i)
            p.text(top_line)
            p.break_()
            p.text(middle_line)
            p.break_()

        bottom_line = self._generate_bottom_line()
        p.text(bottom_line)
        p.break_()
        
    def validate_board_state(self):
        for i in range(self.m):
            for j in range(self.n):
                box = self._boxes[i][j]
                if box.completed:
                    for line in box.lines:
                        if line in self._open_vectors:
                            print(f"Inconsistency found: Closed box at ({i}, {j}) has an open line: {line}")

    def print_board_summary(self):
        print(f"Player Score: {self.player_score}, AI Score: {self.ai_score}")
        print(f"Open vectors: {self._open_vectors}")
        print(f"Moves made: {self._moves}")


In [15]:
Board.display_single_box = True

In [16]:
Board(3, 3)

   *   *   *   *
                
   *   *   *   *
                
   *   *   *   *
                
   *   *   *   *


In [17]:
# from board import Board

board = Board(2, 2)
board

   *   *   *
            
   *   *   *
            
   *   *   *


In [18]:
board.move(((0, 1), (1, 1)))
board

Attempting move: ((0, 1), (1, 1)) by AI
Available moves before: {((1, 1), (2, 1)), ((1, 0), (1, 1)), ((1, 0), (2, 0)), ((0, 0), (0, 1)), ((1, 1), (1, 2)), ((2, 1), (2, 2)), ((0, 2), (1, 2)), ((2, 0), (2, 1)), ((0, 1), (0, 2)), ((0, 1), (1, 1)), ((0, 0), (1, 0)), ((1, 2), (2, 2))}
Available moves after: {((1, 1), (2, 1)), ((1, 0), (1, 1)), ((1, 0), (2, 0)), ((0, 0), (0, 1)), ((1, 1), (1, 2)), ((2, 1), (2, 2)), ((0, 2), (1, 2)), ((2, 0), (2, 1)), ((0, 1), (0, 2)), ((0, 0), (1, 0)), ((1, 2), (2, 2))}
Move resulted in closing box: None


   *   *   *
            
   *---*   *
            
   *   *   *


In [19]:
board._boxes[0][0]

*   *
    
*---*

In [20]:
# %%writefile gamemanager.py
from copy import deepcopy
from typing import Optional
import random

class GameManager:
    
    def __init__(self, m, n, level, mode="minimax"):
        self._level = level
        self._board = Board(m, n)
        self.current_turn = "player"  # El turno inicial es del jugador
        self.last_move = None  # Inicializar last_move

        if mode == "alphabeta":
            self._mode = self.alpha_beta
            print("Using AlphaBeta pruning")
        else:
            self._mode = self.mini_max
            print("Using Minimax")
            
            
    def _repr_pretty_(self, p, cycle):
        if (cycle):
            pass

        # Display player scores
        p.text(f"    AI Score : {self._board.ai_score}\n")
        p.text(f"Player Score : {self._board.player_score}\n")
        self._board._repr_pretty_(p, cycle)

    def get_victor(self):
        print("The game ended")
        print(f"Score: Player={self._board.player_score}, AI={self._board.ai_score}")

        if self._board.player_score > self._board.ai_score:
            return "player"
        elif self._board.player_score < self._board.ai_score:
            return "ai"
        else:
            return "draw"
    
    

    def get_move(self, origin, dest) -> tuple[Optional[tuple[tuple[int, int], tuple[int, int]]], Optional[str]]:
        coordinates = (origin, dest)

        while True:  # Ciclo para manejar turnos adicionales
            result = self._handle_turn(coordinates)
            if result is not None:
                return result

            if not self._board.has_moves():  # Verificar si el juego ha terminado
                return (None, self.get_victor())

    def _handle_turn(self, coordinates) -> Optional[tuple[Optional[tuple[tuple[int, int], tuple[int, int]]], Optional[str]]]:
        if self.current_turn == "player":
            return self._player_move(coordinates)
        elif self.current_turn == "ai":

            return self._ai_move()
        return None
                   
    def _player_move(self, coordinates, is_simulation: bool = False) -> Optional[tuple[Optional[tuple[tuple[int, int], tuple[int, int]]], Optional[str]]]:
        if is_simulation:
            # Crear una copia del estado del tablero para simular
            simulated_board = deepcopy(self._board)
            self.current_turn = "player"  # Cambiar el turno al jugador durante la simulación
            simulated_board.move(coordinates, player_move=True, is_simulation=True)
            self.current_turn = "ai"  # Después de la simulación, cambiar el turno a la IA
            return simulated_board  # Devolver el estado simulado

        # Movimiento real del jugador
        self.current_turn = "player"  # Asegurarse de que es el turno del jugador
        closed_box = self._board.move(coordinates, player_move=True)

        # Actualizar el último movimiento del jugador
        self.last_move = coordinates

        if closed_box:
            print("Player closed a box, gets another turn.")
            if not self._board.has_moves():
                return (None, self.get_victor())
            return None  # El jugador mantiene el turno si cierra una caja

        # Después del movimiento real del jugador, cambiar el turno a la IA
        self.current_turn = "ai"

        self._board.display_board()  # Mostrar el estado del tablero después del movimiento del jugador
        self._board.validate_board_state()  # Verificar consistencia del estado del tablero
        self._board.print_board_summary()  # Imprimir resumen del estado del tablero

        return (None, None)
    
    def _ai_move(self, is_simulation: bool = False) -> Optional[tuple[Optional[tuple[tuple[int, int], tuple[int, int]]], Optional[str]]]:
        """
        Método que maneja el movimiento de la IA.
        
        En la etapa inicial, prioriza movimientos perpendiculares sin simulaciones exhaustivas.
        En etapas posteriores, usa minimax o alpha-beta para decidir el mejor movimiento.
        """
        # Etapa inicial: movimiento directo sin simulaciones
        if self._is_initial_stage():
            print("Initial stage: Selecting perpendicular or random move.")
            move = self._select_perpendicular_or_random_move()
            if move is not None:
                closed_box_ai = self._board.move(move, player_move=False, is_simulation=False)
                self.current_turn = "player"  # Cambiar el turno después de mover
                
                self._board.display_board()
                self._board.validate_board_state()
                self._board.print_board_summary()
                
                if closed_box_ai:
                    print("AI closed a box, gets another turn.")
                    if not self._board.has_moves():  # Verificar si el juego ha terminado
                        return (move, self.get_victor())
                    return None
                return (move, None)
        
        # Etapas medias y finales: usar minimax o alpha-beta
        self.current_turn = "ai"  # Asegurarse de que es el turno de la IA
        eval, best_move = self._mode(self._board, self._level, True)
            
        if best_move is not None:
            closed_box_ai = self._board.move(best_move, player_move=False, is_simulation=False)
            self.current_turn = "player"  # Cambiar el turno después de mover

            self._board.display_board()
            self._board.validate_board_state()
            self._board.print_board_summary()

            if closed_box_ai:
                print("AI closed a box, gets another turn.")
                if not self._board.has_moves():
                    return (best_move, self.get_victor())
                return None

            return (best_move, None)

        return (None, None)




    

    def _select_perpendicular_or_random_move(self) -> Optional[tuple[tuple[int, int], tuple[int, int]]]:
        """
        Selecciona un movimiento que cierre una caja si es posible.
        Si no, selecciona un movimiento perpendicular al último movimiento del jugador sin crear tres líneas.
        Si no hay tal movimiento, selecciona un movimiento aleatorio.
        """
        last_player_move = self.last_move  # Asumiendo que guardas el último movimiento del jugador
        available_moves = list(self._board.get_available_moves())
        random.shuffle(available_moves)  # Mezclar movimientos para aleatoriedad

        # 1. Priorizar movimientos que cierren una caja
        for move in available_moves:
            simulated_state = deepcopy(self._board)
            closed_box = simulated_state.move(move, player_move=False, is_simulation=True)
            if closed_box:
                print(f"Making move to close a box: {move}")
                return move  # Retornar el movimiento que cierra una caja

        # 2. Priorizar movimientos perpendiculares sin riesgo de crear tres líneas
        for move in available_moves:
            if last_player_move and self._is_perpendicular(last_player_move, move):
                if not self._creates_three_lines(self._board, move):
                    return move  # Retornar el movimiento perpendicular seguro

        # 3. Si no hay movimientos perpendiculares válidos, elegir uno aleatorio
        for move in available_moves:
            if not self._creates_three_lines(self._board, move):
                return move  # Retornar el primer movimiento aleatorio seguro encontrado

        # 4. Si todos los movimientos crean tres líneas, seleccionar cualquier movimiento
        return random.choice(available_moves)



    def _is_initial_stage(self) -> bool:
        """
        Determina si el juego está en la etapa inicial.
        """
        total_lines = (self._board.m + 1) * self._board.n + self._board.m * (self._board.n + 1)
        remaining_lines = len(self._board.get_available_moves())
        # Etapa inicial si quedan más del 82.5% de las líneas disponibles
        return remaining_lines > total_lines * 0.825


    def _find_best_move(self, current_state: Board, best_state: Board) -> Optional[tuple[tuple[int, int], tuple[int, int]]]:
        for move in current_state.get_available_moves():
            simulated_state, _ = self.simulate_move(current_state, move, "ai")
            print(f"Checking move: {move}")
            print(f"Simulated state: {simulated_state}")
            print(f"Best state: {best_state}")
            if simulated_state == best_state:
                return move
        print("No matching move found.")
        return None

    @staticmethod
    def simulate_move(state, move, current_turn):
        
        # Realiza una copia profunda del estado para no modificar el original
        simulated_state = deepcopy(state)
        
        # Aplica el movimiento para el jugador actual
        simulated_state.move(move, player_move=(current_turn == "player"), is_simulation=True)
        
        # Cambia el turno para la siguiente simulación
        next_turn = "player" if current_turn == "ai" else "ai"
        
        # Retorna el estado simulado y el próximo turno
        return simulated_state, next_turn


    def mini_max(self, state: Board, ply: int, max_min: bool) -> tuple[float, Board]:
        if ply == 0 or len(state._open_vectors) == 0:
            h = self.evaluate(state)
            return (h, None)
        
        available_moves = list(state.get_available_moves())

        if max_min:
            return self._maximize(state, available_moves, ply)
        else:
            return self._minimize(state, available_moves, ply)


    def _maximize(self, state: Board, available_moves: list, ply: int) -> tuple[float, tuple[int, int]]:
        max_val = float('-inf')
        best_move = None

        for move in available_moves:
            # Simula el movimiento en una copia del tablero
            simulated_state, _ = self.simulate_move(state, move, "ai")
            
            # Evalúa el estado resultante mediante una llamada recursiva a minimax
            eval, _ = self.mini_max(simulated_state, ply - 1, False)
            
            # Si el valor es mejor, guarda el movimiento como el mejor
            if eval > max_val:
                max_val = eval
                best_move = move  # Solo guardas el mejor movimiento

        return (max_val, best_move)


    def _minimize(self, state: Board, available_moves: list, ply: int) -> tuple[float, tuple[int, int]]:
        min_val = float('inf')
        best_move = None

        for move in available_moves:
            # Simula el movimiento en una copia del tablero
            simulated_state, _ = self.simulate_move(state, move, "player")
            
            # Evalúa el estado resultante mediante una llamada recursiva a minimax
            eval, _ = self.mini_max(simulated_state, ply - 1, True)
            
            # Si el valor es mejor, guarda el movimiento como el mejor
            if eval < min_val:
                min_val = eval
                best_move = move  # Solo guardas el mejor movimiento

        return (min_val, best_move)


    def alpha_beta(self, state: Board, ply: int, is_max: bool, alpha=float('-inf'), beta=float('inf')) -> tuple[float, Board]:
        if ply == 0 or not state.has_moves():
            h = self.evaluate(state)
            return (h, None)

        available_moves = list(state.get_available_moves())

        if is_max:
            return self._maximize_alpha_beta(state, available_moves, ply, alpha, beta)
        else:
            return self._minimize_alpha_beta(state, available_moves, ply, alpha, beta)

    def _maximize_alpha_beta(self, state: Board, available_moves: list, ply: int, alpha: float, beta: float) -> tuple[float, tuple[int, int]]:
        max_val = float('-inf')
        best_move = None

        for move in available_moves:
            # Simula el movimiento en una copia del tablero
            simulated_state, _ = self.simulate_move(state, move, "ai")
            
            # Evalúa el estado resultante mediante una llamada recursiva a alpha_beta
            eval, _ = self.alpha_beta(simulated_state, ply - 1, False, alpha, beta)
            
            # Si el valor es mejor, guarda el movimiento como el mejor
            if eval > max_val:
                max_val = eval
                best_move = move  # Solo guardas el mejor movimiento

            # Actualiza alfa
            alpha = max(alpha, max_val)
            
            # Poda alfa-beta
            if beta <= alpha:
                break

        return (max_val, best_move)



    def _minimize_alpha_beta(self, state: Board, available_moves: list, ply: int, alpha: float, beta: float) -> tuple[float, tuple[int, int]]:
        min_val = float('inf')
        best_move = None

        for move in available_moves:
            # Simula el movimiento en una copia del tablero
            simulated_state, _ = self.simulate_move(state, move, "player")
            
            # Evalúa el estado resultante mediante una llamada recursiva a alpha_beta
            eval, _ = self.alpha_beta(simulated_state, ply - 1, True, alpha, beta)
            
            # Si el valor es mejor, guarda el movimiento como el mejor
            if eval < min_val:
                min_val = eval
                best_move = move  # Solo guardas el mejor movimiento

            # Actualiza beta
            beta = min(beta, min_val)
            
            # Poda alfa-beta
            if beta <= alpha:
                break

        return (min_val, best_move)

    
    def evaluate(self, state: Board, last_player_move: Optional[tuple] = None) -> float:
        """
        Evalúa el estado del tablero.
        
        Usa una heurística diferente dependiendo de la etapa del juego.
        """
        total_lines = (state.m + 1) * state.n + state.m * (state.n + 1)
        remaining_lines = len(state._open_vectors)
        
        # Determinar la etapa del juego
        if remaining_lines > total_lines * 0.825:  # Etapa inicial (si son 40 lineas disponibles, hasta que queden 33 líneas)
            return self.evaluate_initial_stage(state, last_player_move)
        elif remaining_lines > total_lines * 0.375:  # Etapa media (si son 40 lineas disponibles, desde 33 hasta 15 líneas)
            return self.evaluate_mid_stage(state)
        else:
            # Etapa final (menos de 15 líneas restantes) - Reemplaza esta parte con la lógica de evaluación que desees para etapas finales
            return self.evaluate_final_stage(state)


    def evaluate_initial_stage(self, state: Board, last_player_move: Optional[tuple]) -> float:
        """
        Evalúa el estado del tablero en la etapa inicial del juego.
        
        La heurística prioriza movimientos que cierren cajas, luego busca movimientos perpendiculares al último movimiento del jugador.
        Si no hay movimientos perpendiculares válidos sin formar tres líneas, selecciona un movimiento aleatorio.

        :param state: Estado actual del tablero.
        :param last_player_move: Último movimiento del jugador (oponente).
        :return: Valor heurístico del estado del tablero.
        """
        ai_score = state.ai_score
        player_score = state.player_score
        
        # Puntaje inicial es la diferencia en puntajes
        heuristic_value = ai_score - player_score

        # Peso para movimientos perpendiculares y evitar movimientos con 3 líneas
        perpendicular_bonus = 5
        avoid_three_lines_penalty = 10
        bonus_for_closing_boxes = 30  # Aumentar el bonus para incentivar el cierre de cajas
        penalty_for_three_lines = 20
        
        # Movimientos posibles
        available_moves = list(state.get_available_moves())
        random.shuffle(available_moves)  # Para que, si seleccionamos un movimiento aleatorio, sea más impredecible

        # 1. Buscar el primer movimiento que cierre una caja
        for move in available_moves:
            simulated_state = deepcopy(state)
            closed_box = simulated_state.move(move, player_move=False, is_simulation=True)
            if closed_box:
                print(f"Making move to close a box: {move}")
                return heuristic_value + bonus_for_closing_boxes

        # 2. Buscar el primer movimiento perpendicular que no forme tres líneas
        for move in available_moves:
            if last_player_move and self._is_perpendicular(last_player_move, move):
                # Verificar si el movimiento crearía tres líneas en una caja
                if not self._creates_three_lines(state, move):
                    print(f"Making perpendicular move: {move}")
                    # Hacer el movimiento y retornar el valor heurístico actual
                    return heuristic_value + perpendicular_bonus

        # 3. Si no se encuentra un movimiento perpendicular válido, elegir un movimiento aleatorio
        for move in available_moves:
            simulated_state = deepcopy(state)
            closed_box = simulated_state.move(move, player_move=False, is_simulation=True)
            
            move_score = 0
            
            if closed_box:
                move_score += bonus_for_closing_boxes
            if self._creates_three_lines(state, move):
                move_score -= penalty_for_three_lines
            
            heuristic_value += move_score
            print(f"Making random move: {move}")
            break  # Realiza el primer movimiento encontrado sin más simulaciones

        return heuristic_value

    

    def _is_perpendicular(self, last_move: tuple, current_move: tuple) -> bool:
        """
        Verifica si el movimiento actual es perpendicular al último movimiento del jugador y
        comparte un punto de partida con el movimiento del jugador.
        
        :param last_move: Último movimiento del jugador.
        :param current_move: Movimiento actual a verificar.
        :return: True si es perpendicular y comparte un punto de partida, False de lo contrario.
        """
        (x1, y1), (x2, y2) = last_move
        (a1, b1), (a2, b2) = current_move

        # Verificar si la primera línea es horizontal
        last_move_is_horizontal = (x1 == x2 and y1 != y2)
        # Verificar si la segunda línea es vertical
        current_move_is_vertical = (a1 != a2 and b1 == b2)

        # Verificar si la primera línea es vertical
        last_move_is_vertical = (y1 == y2 and x1 != x2)
        # Verificar si la segunda línea es horizontal
        current_move_is_horizontal = (b1 != b2 and a1 == a2)

        # Verificar si hay un punto de partida compartido entre las líneas
        shared_start_or_end = (
            (x1, y1) == (a1, b1) or (x1, y1) == (a2, b2) or
            (x2, y2) == (a1, b1) or (x2, y2) == (a2, b2)
        )

        # Retorna True si uno es horizontal y el otro es vertical y comparten un punto
        return shared_start_or_end and (
            (last_move_is_horizontal and current_move_is_vertical) or
            (last_move_is_vertical and current_move_is_horizontal)
        )

    def evaluate_mid_stage(self, state: Board) -> float:
        """
        Evalúa el estado del tablero en la etapa media del juego.
        
        La heurística prioriza cerrar cajas siempre que sea posible, evita la creación de cadenas largas 
        impares desfavorables, y penaliza dejar 3 líneas en una caja.

        :param state: Estado actual del tablero.
        :return: Valor heurístico del estado del tablero.
        """
        ai_score = state.ai_score
        player_score = state.player_score
        
        # Puntaje inicial es la diferencia en puntajes
        heuristic_value = ai_score - player_score
        
        # Detectar todas las cadenas de líneas en el tablero
        chains = self._detect_chains(state)
        
        # Peso de penalización para cadenas impares y bonificación para cerrar cajas
        penalty_for_odd_chains = 15
        bonus_for_closing_boxes = 30  # Aumentar el bonus para incentivar el cierre de cajas
        penalty_for_three_lines = 20
        
        # Penalizar cadenas largas de longitud impar y bonificar pares
        for chain in chains:
            if len(chain) % 2 != 0:  # Cadena de longitud impar
                heuristic_value -= penalty_for_odd_chains  # Penalización para cadenas impares
            else:
                heuristic_value += penalty_for_odd_chains  # Bonificación para cadenas pares
        
        # Priorizar movimientos que cierren cuadrados y penalizar dejar 3 líneas
        for move in state.get_available_moves():
            # Simular el movimiento
            simulated_state = deepcopy(state)
            closed_box = simulated_state.move(move, player_move=False, is_simulation=True)
            
            if closed_box:
                heuristic_value += bonus_for_closing_boxes
            elif self._creates_three_lines(state, move):
                heuristic_value -= penalty_for_three_lines
        
        return heuristic_value

    
    def _detect_chains(self, state: Board):
        """
        Detecta todas las cadenas de líneas en el tablero.
        
        Una cadena se forma cuando hay una secuencia de líneas paralelas dibujadas en una fila o columna.
        
        :param state: Estado actual del tablero.
        :return: Lista de cadenas detectadas, donde cada cadena es una lista de líneas conectadas.
        """
        chains = []

        # Detectar cadenas horizontales
        for i in range(state.m + 1):  # Incluye todas las filas posibles
            current_chain = []
            for j in range(state.n):  # Recorrer columnas
                if ((j, i), (j + 1, i)) in state._moves:  # Línea horizontal entre (j, i) y (j+1, i)
                    current_chain.append(((j, i), (j + 1, i)))
                else:
                    # Si encontramos un fin de cadena, la añadimos
                    if len(current_chain) > 1:
                        chains.append(current_chain)
                    current_chain = []  # Reiniciar la cadena

            # Si la cadena termina al final de la fila, añadirla
            if len(current_chain) > 1:
                chains.append(current_chain)

        # Detectar cadenas verticales
        for j in range(state.n + 1):  # Incluye todas las columnas posibles
            current_chain = []
            for i in range(state.m):  # Recorrer filas
                if ((j, i), (j, i + 1)) in state._moves:  # Línea vertical entre (j, i) y (j, i+1)
                    current_chain.append(((j, i), (j, i + 1)))
                else:
                    # Si encontramos un fin de cadena, la añadimos
                    if len(current_chain) > 1:
                        chains.append(current_chain)
                    current_chain = []  # Reiniciar la cadena

            # Si la cadena termina al final de la columna, añadirla
            if len(current_chain) > 1:
                chains.append(current_chain)

        return chains


    def _explore_chain(self, state: Board, start_box, visited: set):
        """
        Explora una cadena comenzando desde una caja específica.
        
        :param state: Estado actual del tablero.
        :param start_box: Caja desde la cual comenzar la exploración.
        :param visited: Conjunto de cajas ya visitadas.
        :return: Lista de cajas que forman la cadena.
        """
        chain = []
        stack = [start_box]

        while stack:
            (i, j) = stack.pop()
            if (i, j) in visited:
                continue

            visited.add((i, j))
            chain.append((i, j))

            # Obtener cajas adyacentes que comparten una línea común
            for adj_box in self._get_adjacent_boxes(state, i, j):
                if adj_box not in visited:
                    stack.append(adj_box)

        return chain

    def _get_adjacent_boxes(self, state: Board, i: int, j: int):
        """
        Obtiene las cajas adyacentes que comparten una línea común con la caja (i, j).
        
        :param state: Estado actual del tablero.
        :param i: Índice de la fila de la caja.
        :param j: Índice de la columna de la caja.
        :return: Lista de coordenadas de cajas adyacentes.
        """
        adjacent_boxes = []
        current_box = state._boxes[i][j]

        # Verificar las líneas para encontrar cajas adyacentes conectadas
        if current_box._right and j + 1 < state.n:  # Caja a la derecha
            adjacent_boxes.append((i, j + 1))
        if current_box._left and j - 1 >= 0:  # Caja a la izquierda
            adjacent_boxes.append((i, j - 1))
        if current_box._top and i - 1 >= 0:  # Caja arriba
            adjacent_boxes.append((i - 1, j))
        if current_box._bottom and i + 1 < state.m:  # Caja abajo
            adjacent_boxes.append((i + 1, j))

        return adjacent_boxes
    def evaluate_final_stage(self, state: Board) -> float:
        """
        Evalúa el estado del tablero en la etapa final del juego.
        
        La heurística prioriza completar la mayor cantidad posible de cajas para maximizar el puntaje.
        
        :param state: Estado actual del tablero.
        :return: Valor heurístico del estado del tablero.
        """
        ai_score = state.ai_score
        player_score = state.player_score
        
        # Puntaje inicial es la diferencia en puntajes
        heuristic_value = ai_score - player_score

        # Priorizar movimientos que cierren el mayor número posible de cajas
        max_boxes_to_close = 0

        for move in state.get_available_moves():
            # Simular el movimiento
            simulated_state = deepcopy(state)
            boxes_closed = 0
            
            # Aplicar el movimiento simulado
            closed_box = simulated_state.move(move, player_move=False, is_simulation=True)
            while closed_box:
                boxes_closed += 1
                # Simular otro movimiento después de cerrar una caja
                next_moves = simulated_state.get_available_moves()
                if not next_moves:
                    break
                next_move = next_moves.pop()
                closed_box = simulated_state.move(next_move, player_move=False, is_simulation=True)

            # Actualizar el valor heurístico para maximizar las cajas cerradas
            max_boxes_to_close = max(max_boxes_to_close, boxes_closed)
        
        # Añadir el beneficio de cerrar cajas al valor heurístico
        heuristic_value += max_boxes_to_close * 10  # Ajusta este peso según sea necesario
        
        return heuristic_value
    
    def _creates_three_lines(self, state: Board, move: tuple) -> bool:
        """
        Verifica si un movimiento dado resultará en tres líneas conectadas en una caja.
        
        :param state: Estado actual del tablero.
        :param move: Movimiento a verificar.
        :return: True si el movimiento crea una situación de tres líneas, False de lo contrario.
        """
        # Hacemos una copia del estado del tablero para simular el movimiento
        simulated_state = deepcopy(state)
        simulated_state.move(move, player_move=False, is_simulation=True)
        
        # Recorremos todas las cajas y verificamos si alguna tiene exactamente tres líneas conectadas
        for i in range(simulated_state.m):
            for j in range(simulated_state.n):
                box = simulated_state._boxes[i][j]
                connected_lines = sum([box._top, box._left, box._right, box._bottom])
                
                if connected_lines == 3:
                    return True  # Se crea una situación de tres líneas
        
        return False




In [21]:
import random

class Tester:
    def __init__(self, board_size=(4, 4), level=3, mode="minimax"):
        self.board_size = board_size
        self.level = level
        self.mode = mode
        self.game_manager = GameManager(board_size[0], board_size[1], level, mode)
    
    def simulate_random_player_vs_ai(self):
        print("\nStarting a new game: Player (random) vs AI")
        self.game_manager = GameManager(self.board_size[0], self.board_size[1], self.level, self.mode)
        print(f"Player starts the game!")

        while self.game_manager._board.has_moves():
            if self.game_manager.current_turn == "player":
                # Movimiento aleatorio del jugador
                move = random.choice(list(self.game_manager._board.get_available_moves()))
                print(f"\nPlayer's turn. Attempting move: {move}")  # Imprimir las coordenadas del movimiento del jugador
                self.game_manager.get_move(*move)
            else:
                print("\nAI's turn.")
                move, _ = self.game_manager.get_move(None, None)  # La IA toma su turno
                if move is not None:
                    print(f"AI attempts move: {move}")  # Imprimir las coordenadas del movimiento de la IA
                    heuristic_value = self.game_manager.evaluate(self.game_manager._board)
                    print(f"Heuristic Value after AI move: {heuristic_value}")
            
            # Imprimir puntuaciones después de cada movimiento
            self.print_scores()

        victor = self.game_manager.get_victor()
        print(f"\nGame Over! The winner is: {victor}")
        return victor

    def simulate_ai_vs_ai(self):
        print("\nStarting a new game: AI vs AI")
        self.game_manager = GameManager(self.board_size[0], self.board_size[1], self.level, self.mode)
        print(f"AI ({self.mode}) starts the game!")
        self.game_manager.current_turn = "ai"  # Forzar que inicie la IA

        while self.game_manager._board.has_moves():
            if self.game_manager.current_turn == "ai":
                print(f"\nAI's turn using {self.mode} strategy.")
                move, _ = self.game_manager.get_move(None, None)
                if move is not None:
                    print(f"AI attempts move: {move}")  # Imprimir las coordenadas del movimiento de la IA
                    heuristic_value = self.game_manager.evaluate(self.game_manager._board)
                    print(f"Heuristic Value after AI move: {heuristic_value}")
            else:
                move = random.choice(list(self.game_manager._board.get_available_moves()))
                print(f"Opponent AI attempts random move: {move}")  # Imprimir las coordenadas del movimiento de la IA oponente
                self.game_manager.get_move(*move)
            
            # Imprimir puntuaciones después de cada movimiento
            self.print_scores()
        
        victor = self.game_manager.get_victor()
        print(f"\nGame Over! The winner is: {victor}")
        return victor

    def analyze_performance(self, num_games=10, mode="random_vs_ai"):
        results = {"player_wins": 0, "ai_wins": 0, "draws": 0}

        for i in range(num_games):
            if mode == "random_vs_ai":
                print(f"\nSimulating Game {i+1} - Random Player vs AI")
                victor = self.simulate_random_player_vs_ai()
            elif mode == "ai_vs_ai":
                print(f"\nSimulating Game {i+1} - AI vs AI")
                victor = self.simulate_ai_vs_ai()

            if victor == "player":
                results["player_wins"] += 1
            elif victor == "ai":
                results["ai_wins"] += 1
            else:
                results["draws"] += 1

        print(f"\nResults after {num_games} games ({mode}):")
        print(f"Player Wins: {results['player_wins']}")
        print(f"AI Wins: {results['ai_wins']}")
        print(f"Draws: {results['draws']}")
        return results

    def print_scores(self):
        print(f"\nCurrent Scores:")
        print(f"Player: {self.game_manager._board.player_score}")
        print(f"AI: {self.game_manager._board.ai_score}")


In [22]:
# Inicializar el tester
tester = Tester(board_size=(3, 3), level=2, mode="alphabeta")

# Simular un juego con jugador aleatorio vs IA
tester.simulate_random_player_vs_ai()


Using AlphaBeta pruning

Starting a new game: Player (random) vs AI
Using AlphaBeta pruning
Player starts the game!

Player's turn. Attempting move: ((0, 0), (1, 0))
Attempting move: ((0, 0), (1, 0)) by Player
Available moves before: {((1, 2), (1, 3)), ((2, 2), (3, 2)), ((1, 1), (2, 1)), ((1, 0), (2, 0)), ((2, 1), (2, 2)), ((1, 3), (2, 3)), ((0, 1), (0, 2)), ((1, 1), (1, 2)), ((1, 2), (2, 2)), ((0, 0), (1, 0)), ((0, 2), (0, 3)), ((3, 0), (3, 1)), ((0, 3), (1, 3)), ((2, 1), (3, 1)), ((2, 0), (2, 1)), ((0, 1), (1, 1)), ((2, 3), (3, 3)), ((1, 0), (1, 1)), ((0, 0), (0, 1)), ((0, 2), (1, 2)), ((3, 2), (3, 3)), ((3, 1), (3, 2)), ((2, 0), (3, 0)), ((2, 2), (2, 3))}
Available moves after: {((1, 2), (1, 3)), ((2, 2), (3, 2)), ((1, 1), (2, 1)), ((1, 0), (2, 0)), ((2, 1), (2, 2)), ((1, 3), (2, 3)), ((0, 1), (0, 2)), ((1, 1), (1, 2)), ((1, 2), (2, 2)), ((0, 2), (0, 3)), ((3, 0), (3, 1)), ((0, 3), (1, 3)), ((2, 1), (3, 1)), ((2, 0), (2, 1)), ((0, 1), (1, 1)), ((2, 3), (3, 3)), ((1, 0), (1, 1)), ((0

'ai'

In [23]:

# # Simular un juego de IA vs IA
# tester.simulate_ai_vs_ai()



In [24]:
# # Analizar el rendimiento en múltiples juegos
# performance_results = tester.analyze_performance(num_games=10)